In [1]:
from transformers import BertTokenizer, AutoConfig, AutoModelForSequenceClassification

tokenizer = BertTokenizer.from_pretrained('bert-base-cased')
model = AutoModelForSequenceClassification.from_pretrained("bert-base-cased-offline", num_labels=2)

In [2]:
from glob import glob
from datasets import Dataset

import re
import pandas as pd

def data_loading(url):
    with open(url, 'r', encoding='utf-8') as f:
        # data = json.loads(f.read())
        df = pd.read_json(f)
        data = df.copy()
        # data = df.loc[:, ['sentiment', 'body']]
        data = data.loc[df['sentiment'].notnull()]
        data['sentiment'] = pd.Categorical(data['sentiment'])
        data['label'] = data['sentiment'].cat.codes
        data = data.rename(columns={'sentiment': 'labels', 'body': 'sentense'})

        return data

data_url = '../crawler/stock/data/**.json'
url = glob(data_url)[-1]
data = data_loading(url)

dataset = Dataset.from_pandas(data.loc[:, ['label', 'sentense']])
dataset = dataset.remove_columns('__index_level_0__')

In [3]:
def encode(example):
    result = tokenizer(example['sentense'], padding='max_length', truncation=True)
    return result

encoded_dataset = dataset.map(encode, batched=True)
encoded_dataset = encoded_dataset.train_test_split(test_size=0.2)
# print(encoded_dataset[0]['sentense'])
# print(encoded_dataset[0]['input_ids'])
# type(encoded_dataset[0]['labels'])

100%|██████████| 15/15 [00:06<00:00,  2.25ba/s]


In [4]:
from transformers import TrainingArguments, Trainer
from datasets import load_metric

import numpy as np
import wandb

%env WANDB_PROJECT=Stocktwit_sentiment_analysis
training_args = TrainingArguments(
    output_dir="bert-classifier-trainer",
    evaluation_strategy="steps",
    eval_steps=100,
    num_train_epochs=10,
    save_steps=5000,
    per_device_train_batch_size=4,
    report_to="wandb",
    run_name="bert-sentiment-classifier-test-10-epoch"
)

recall_metric = load_metric("recall")
precision_metric = load_metric("precision")


def compute_metrics(eval_pred):
    logits, labels = eval_pred
    predictions = np.argmax(logits, axis=-1)
    result = recall_metric.compute(predictions=predictions, references=labels)
    result.update(precision_metric.compute(predictions=predictions, references=labels))
    return result

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=encoded_dataset['train'],
    eval_dataset=encoded_dataset['test'],
    compute_metrics=compute_metrics,
)

trainer.train()

wandb.finish()

env: WANDB_PROJECT=Stocktwit_sentiment_analysis


The following columns in the training set  don't have a corresponding argument in `BertForSequenceClassification.forward` and have been ignored: sentense. If sentense are not expected by `BertForSequenceClassification.forward`,  you can safely ignore this message.
C:\Users\douli\anaconda3\envs\stock-nlp\lib\site-packages\transformers\optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 11353
  Num Epochs = 10
  Instantaneous batch size per device = 4
  Total train batch size (w. parallel, distributed & accumulation) = 4
  Gradient Accumulation steps = 1
  Total optimization steps = 28390
Automatic Weights & Biases logging enabled, to disable set os.environ["WANDB_DISABLED"] = "true"
Failed to detect the name of this notebook, you can set it 

  0%|          | 100/28390 [00:30<2:15:15,  3.49it/s]The following columns in the evaluation set  don't have a corresponding argument in `BertForSequenceClassification.forward` and have been ignored: sentense. If sentense are not expected by `BertForSequenceClassification.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 2839
  Batch size = 8

  0%|          | 100/28390 [01:36<2:15:15,  3.49it/s]

{'eval_loss': 0.6303860545158386, 'eval_recall': 1.0, 'eval_precision': 0.6706586826347305, 'eval_runtime': 66.8077, 'eval_samples_per_second': 42.495, 'eval_steps_per_second': 5.314, 'epoch': 0.04}


  1%|          | 200/28390 [02:05<2:17:30,  3.42it/s]  The following columns in the evaluation set  don't have a corresponding argument in `BertForSequenceClassification.forward` and have been ignored: sentense. If sentense are not expected by `BertForSequenceClassification.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 2839
  Batch size = 8

  1%|          | 200/28390 [03:12<2:17:30,  3.42it/s]

...

{'eval_loss': 0.5888465642929077, 'eval_recall': 0.9065126050420168, 'eval_precision': 0.7215719063545151, 'eval_runtime': 62.4989, 'eval_samples_per_second': 45.425, 'eval_steps_per_second': 5.68, 'epoch': 9.93}


100%|█████████▉| 28300/28390 [7:02:57<00:24,  3.66it/s]The following columns in the evaluation set  don't have a corresponding argument in `BertForSequenceClassification.forward` and have been ignored: sentense. If sentense are not expected by `BertForSequenceClassification.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 2839
  Batch size = 8
                                                       
100%|█████████▉| 28300/28390 [7:04:00<00:24,  3.66it/s]

{'eval_loss': 0.5892309546470642, 'eval_recall': 0.9096638655462185, 'eval_precision': 0.7204658901830283, 'eval_runtime': 62.4787, 'eval_samples_per_second': 45.439, 'eval_steps_per_second': 5.682, 'epoch': 9.97}


100%|█████████▉| 28389/28390 [7:04:24<00:00,  3.68it/s]

Training completed. Do not forget to share your model on huggingface.co/models =)


100%|██████████| 28390/28390 [7:04:24<00:00,  1.11it/s]


{'train_runtime': 25467.3883, 'train_samples_per_second': 4.458, 'train_steps_per_second': 1.115, 'train_loss': 0.6397343005710775, 'epoch': 10.0}



In [5]:
a = encoded_dataset['train']
a['input_ids']

[[101,
  109,
  157,
  13726,
  1592,
  146,
  1567,
  12008,
  26597,
  1133,
  1141,
  1144,
  1106,
  1129,
  13142,
  1142,
  1110,
  1103,
  1141,
  4482,
  1114,
  7302,
  1105,
  6998,
  1115,
  1144,
  1136,
  12235,
  4984,
  1105,
  1165,
  1122,
  1674,
  1122,
  1209,
  1930,
  4344,
  1103,
  3248,
  1107,
  1139,
  4893,
  119,
  9255,
  2944,
  1263,
  1858,
  1133,
  1603,
  1858,
  1122,
  1198,
  3093,
  1176,
  1122,
  1209,
  2760,
  1106,
  1243,
  1260,
  6617,
  22733,
  102,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
 

In [6]:
model.save_pretrained('./bert-classifier-trainer/test-epoch-1')

Configuration saved in ./bert-classifier-trainer/test-epoch-1\config.json
Model weights saved in ./bert-classifier-trainer/test-epoch-1\pytorch_model.bin
